In [1]:
import tensorflow as tf
import keras
import numpy as np
import cv2
import os
# import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from tensorflow.keras import datasets, layers, models
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.metrics import BinaryAccuracy
from tensorflow.keras.layers import Dense
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
import matplotlib.pyplot as plt
from sklearn import metrics
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

2023-04-18 17:31:39.768285: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-04-18 17:31:40.802646: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-04-18 17:31:40.805211: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-04-18 17:31:55.327064: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [21]:
#!unzip -a "../data/train_100.zip" -d "../content"

Archive:  ../data/train_100.zip
   creating: ../content/100/
  inflating: ../content/__MACOSX/._100  [binary]
  inflating: ../content/100/.DS_Store  [binary]
  inflating: ../content/__MACOSX/100/._.DS_Store  [binary]
   creating: ../content/100/0/
  inflating: ../content/__MACOSX/100/._0  [binary]
   creating: ../content/100/1/
  inflating: ../content/__MACOSX/100/._1  [binary]
   creating: ../content/100/3/
  inflating: ../content/__MACOSX/100/._3  [binary]
   creating: ../content/100/2/
  inflating: ../content/__MACOSX/100/._2  [binary]
  inflating: ../content/100/0/80054.jpg  [binary]
  inflating: ../content/__MACOSX/100/0/._80054.jpg  [binary]
  inflating: ../content/100/0/823.jpg  [binary]
  inflating: ../content/__MACOSX/100/0/._823.jpg  [binary]
  inflating: ../content/100/0/15259.jpg  [binary]
  inflating: ../content/__MACOSX/100/0/._15259.jpg  [binary]
  inflating: ../content/100/0/4217.jpg  [binary]
  inflating: ../content/__MACOSX/100/0/._4217.jpg  [binary]
  inflating: ../c

In [2]:
def readImages(folder_name, num):
    images = []
    count = 0
    for name in os.listdir(folder_name):
        try:
            img = cv2.imread(folder_name + name, cv2.IMREAD_GRAYSCALE).reshape(100, 100, 1)
        except:
            print(name)
        images.append(img)
        count += 1
        if count == num:
            break
    matrix = np.stack(images, axis=0)
    return matrix

In [3]:
images_0 = readImages('../content/100/0/', 5000)
images_1 = readImages('../content/100/1/', 5000)
images_2 = readImages('../content/100/2/', 5000)
images_3 = readImages('../content/100/3/', 5000)

.DS_Store
.DS_Store


In [4]:
print(images_0.shape)
print(images_1.shape)
print(images_2.shape)
print(images_3.shape)

(5000, 100, 100, 1)
(5000, 100, 100, 1)
(5000, 100, 100, 1)
(5000, 100, 100, 1)


In [5]:
labels_0 = np.zeros((5000,1), int)
labels_1 = np.ones((5000,1), int)
labels_2 = np.zeros((5000,1), int)
labels_2.fill(2)
labels_3 = np.zeros((5000,1), int)
labels_3.fill(3)
print(labels_0.shape)
print(labels_1.shape)
print(labels_2.shape)
print(labels_3.shape)

(5000, 1)
(5000, 1)
(5000, 1)
(5000, 1)


In [6]:
labels = np.concatenate((labels_0, labels_1, labels_2, labels_3), axis=0)

In [7]:
images = np.vstack((images_0, images_1, images_2, images_3))

In [8]:
train_images, test_images, train_labels, test_labels = train_test_split(images, labels, test_size=0.2, random_state=42)

In [9]:
train_images = train_images.astype('float32') / 255
test_images = test_images.astype('float32') / 255

In [10]:
train_images = np.reshape(train_images, (16000, 10000))
test_images = np.reshape(test_images, (4000, 10000))

In [11]:
train_labels = train_labels.flatten()
test_labels = test_labels.flatten()

In [12]:
print(train_images.shape)
print(train_labels.shape)
print(test_images.shape)
print(test_labels.shape)

(16000, 10000)
(16000,)
(4000, 10000)
(4000,)


### Validation data preprocessing

In [13]:
#!unzip -a "../data/Validation_100.zip" -d "../content"

In [14]:
count = 500

In [15]:
images_val_0 = readImages('../content/Validation_100/0/', count)
images_val_1 = readImages('../content/Validation_100/1/', count)
images_val_2 = readImages('../content/Validation_100/2/', count)
images_val_3 = readImages('../content/Validation_100/3/', count)

In [16]:
validation_images = np.vstack((images_val_0, images_val_1, images_val_2, images_val_3))
val_images = validation_images.astype('float32') / 255

In [17]:
labels_val_0 = np.zeros((count,1), int)
labels_val_1 = np.ones((count,1), int)
labels_val_2 = np.zeros((count,1), int)
labels_val_2.fill(2)
labels_val_3 = np.zeros((count,1), int)
labels_val_3.fill(3)
print(labels_val_0.shape)
print(labels_val_1.shape)
print(labels_val_2.shape)
print(labels_val_3.shape)

(500, 1)
(500, 1)
(500, 1)
(500, 1)


In [18]:
print(val_images.shape)

(2000, 100, 100, 1)


In [19]:
val_images = np.reshape(val_images, (2000, 10000))

In [20]:
val_labels = np.concatenate((labels_val_0, labels_val_1, labels_val_2, labels_val_3), axis=0)

In [21]:
val_labels = val_labels.flatten()

In [22]:
print(train_images.shape)
print(train_labels.shape)
print(val_images.shape)
print(val_labels.shape)

(16000, 10000)
(16000,)
(2000, 10000)
(2000,)


### Vis setup

In [23]:
def plotConfusionMatrix(y_pred, test_labels):
    confusion_matrix = metrics.confusion_matrix(y_pred, test_labels, normalize='true')

    disp = metrics.ConfusionMatrixDisplay(confusion_matrix=confusion_matrix, display_labels=["0", "1", "2", "3"])
    disp.plot()

    plt.show()

### SVM Hyperparameter

In [24]:
from sklearn.model_selection import GridSearchCV

In [ ]:
params = {
    'C': [0.1, 1, 10, 100],
    'gamma': [1, 0.1, 0.01],
    'kernel': ['rbf', 'poly']
}

clf = GridSearchCV(
    estimator=SVC(),
    param_grid=params
#     cv=5,
#     n_jobs=5,
#     verbose=1
)

clf.fit(train_images, train_labels)

In [ ]:
print(clf.best_params_)

In [ ]:
predictions = clf.predict(val_images)
accuracy = accuracy_score(val_labels, predictions)

In [ ]:
accuracy

In [ ]:
plotConfusionMatrix(predictions, val_labels)

### SVM polynomial kernal

In [ ]:
svm2 = SVC(kernel='poly')
svm2.fit(train_images, train_labels)

In [ ]:
y_pred = svm2.predict(val_images)
accuracy2 = accuracy_score(val_labels, y_pred)
accuracy2

In [ ]:
plotConfusionMatrix(y_pred, val_labels)

### SVM RBF kernal

In [ ]:
svm3 = SVC(kernel = 'rbf')
svm3.fit(train_images, train_labels)

In [ ]:
y_pred2 = svm3.predict(val_images)
accuracy2 = accuracy_score(val_labels, y_pred2)
accuracy2

In [ ]:
plotConfusionMatrix(y_pred2, val_labels)